## Hot air balloon - lift calculator
### Inverted pyramid shape
[Source code](https://gitea.citizen4.eu/sp9unb/balloon-calc) 

[Run in mybinder.org IDE](https://mybinder.org/v2/git/https%3A%2F%2Fgitea.citizen4.eu%2Fsp9unb%2Fballoon-calc/HEAD?labpath=work%2Fhotair-pyramid.ipynb) 

In [1]:
# https://pythreejs.readthedocs.io
from pythreejs import *
from IPython.display import HTML,display
from math import pi

# https://ipywidgets.readthedocs.io
import ipywidgets as widgets
from ipywidgets import Layout

# https://pypi.org/project/termcolor/
from termcolor import colored

#from scipy.interpolate import interp1d
#import numpy as np

#math
from math import sin, tan, sqrt

In [2]:
# air density–temperature relationship at 1 atm or 101.325 kPa
# https://en.wikipedia.org/wiki/Density_of_air
# https://www.engineersedge.com/calculators/air-density.htm
# temp in st.C   density in g/m3

#temp = [-25,-20,-15,-10,-5,0,5,10,15,20,25,30,35]
#dens = [1422.4,1394.3,1367.3,1341.3,1316.3,1292.2,1269.0,1246.6,1225.0,1204.1,1183.9,1164.4,1145.5]
#dens_temp_func = interp1d(temp, dens)


def airDensity(temp=0.0):
    tempK = temp + 273.0   # absolute temperature [K]
    p = 101325.0           # pressure [Pa]
    rSpec = 287.0500676    # specific gas constant for dry air [J⋅kg−1⋅K−1]
    return 1000.0 * p / ( rSpec * tempK )

In [3]:
# math: https://pl.wikipedia.org/wiki/Wielok%C4%85t_foremny

# radius of the circle described on the polygon
def outradius(a=1.0,n=3):
    return a / ( 2 * sin( pi / n ))

# radius of the circle inscribed in the polygon
def inradius(a=1.0,n=3):
    return a / ( 2 * tan( pi / n ))   

# edge length
def edge_len(r=1.0,h=1.0):
    return sqrt(pow(r,2) + pow(h,2))

#pyramid area/volume
def base_area(a=1.0,n=3):
    return 0.5 * n * pow(outradius(a,n),2) * sin( 2 * pi / n)

def volume(a=1.0,h1=1.0,h2=1.0,n=3):
    return base_area(a,n) * ( h1 + h2 ) / 3
           
def surface_area(a=1.0,h1=1.0,h2=1.0,n=3):
    return 0.5 * a * n * ( sqrt( pow(h1,2) + pow(inradius(a,n),2)) + sqrt( pow(h2,2) + pow(inradius(a,n),2)) )
            


In [5]:
def f(num,width,heightT,heightB,airTemp,hotAirTemp,coatDens,tapeDens,payloadWeight):

    out=widgets.Output(layout={'margin': '10px 10px 10px 20px'})     
    with out:        
    # Volume
        vol = volume(width,heightB,heightT,num)
        print( "Volume: {:.2f} [m3]".format(vol)) 
    # Area
        area = surface_area(width,heightB,heightT,num)
        print( "Area: {:.2f} [m2]".format(area)) 
    # Coating density (from: protective film for painting): 300g / 4x5m = 15g/m2   
        coatingWeight = coatDens * area
        print( "Coating weight: {:.2f} [g]".format(coatingWeight))  
    # adhesive tape density : average 2g/m   
        tapeLength = num * ( edge_len(outradius(width,num),heightT) + edge_len(outradius(width,num),heightB)  )
        tapeWeight = tapeDens * tapeLength
        print( "Adh.tape length: {:.2f} [m]".format(tapeLength))          
        print( "Adh.tape weight: {:.2f} [g]".format(tapeWeight))          
    # Lift per volume g/m3  
    #    airDens = dens_temp_func( airTemp )
    #    hotAirDens = dens_temp_func( hotAirTemp )    
        airDens = airDensity( airTemp )
        hotAirDens = airDensity( hotAirTemp )  
        lift = airDens - hotAirDens
        print( "Lift: {:.2f} [g/m3]".format(lift))      
    # Total lift force  lift * volume 
        totalLiftForce = lift * vol
        print( "Total lift force: {:.2f} [g]".format(totalLiftForce))    
    # Free lift force totalLiftForce - coatingWeight 
        freeLiftForce = totalLiftForce - coatingWeight - tapeWeight - payloadWeight
        if freeLiftForce < 0:
            color = 'red'
        else:
            color = None
        print( "Free lift force:", colored("{:.2f} [g]".format(freeLiftForce),color))  

    
# coating geometry    
    bottomGeometry = CylinderBufferGeometry(
                            radiusTop=outradius(width,num), 
                            radiusBottom=0.0, 
                            height=heightB, 
                            radialSegments=num, 
                            heightSegments=1, 
                            openEnded=True, 
                            thetaStart=0, 
                            thetaLength=2.0*pi)
    
    bottomCylinder = Mesh(bottomGeometry,
                          material=MeshLambertMaterial(color='#c0c0c0'),
                          position=[0,0,0]      
                   )
    
    zTop = ( heightB + heightT ) / 2.0
    topGeometry = CylinderBufferGeometry(
                            radiusTop=0.0, 
                            radiusBottom=outradius(width,num), 
                            height=heightT, 
                            radialSegments=num, 
                            heightSegments=1, 
                            openEnded=True, 
                            thetaStart=0, 
                            thetaLength=2.0*pi)
    
    topCylinder = Mesh(topGeometry,
                          material=MeshLambertMaterial(color='#c0c0c0'),
                          position=[0,zTop,0]      
                   )    
    
    keyLight = DirectionalLight(color='white', position=[3, 5, 1], intensity=0.5)

    c = PerspectiveCamera(position=[2, 2, 6], up=[0, 1, 0], children=[keyLight])

    scene = Scene(children=[bottomCylinder,topCylinder, c, AmbientLight(color='#777777')], background=None)

    renderer = Renderer(camera=c,
                        scene=scene,
                        alpha=True,
                        clearOpacity=1.0,
                        clearColor='#62a0ea',
                        controls=[OrbitControls(controlling=c)])
    display(widgets.HBox([renderer, out]))  



display(HTML('''<style>
     .widget-hbox  { margin-top: 20px; }
 </style>'''))

layout=Layout(width='500px')
style = {'description_width': 'initial'}
  
num=widgets.IntSlider(min=3, max=12, step=1, value=3, description='Segment num:',layout=layout,style=style)     
width=widgets.FloatSlider(min=0.1, max=5.0, step=0.1, value=3.0, description='Segment width [m]:',readout_format='.1f',layout=layout,style=style) 
heightT=widgets.FloatSlider(min=0.1, max=5.0, step=0.1, value=1.0, description='Height top [m]:',readout_format='.1f',layout=layout,style=style) 
heightB=widgets.FloatSlider(min=0.1, max=5.0, step=0.1, value=2.0, description='Height bottom [m]:',readout_format='.1f',layout=layout,style=style) 
airTemp=widgets.FloatSlider(min=-40, max=35, step=1.0, value=10.0, description='Air temp.[°C]:',readout_format='.0f',layout=layout,style=style) 
hotAirTemp=widgets.FloatSlider(min=-40, max=55, step=1.0, value=35.0, description='Hot air temp.[°C]:',readout_format='.0f',layout=layout,style=style)
coatDens=widgets.FloatSlider(min=1, max=50, step=1.0, value=15.0, description='Coating density [g/m2]:',readout_format='.0f',layout=layout,style=style)   
tapeDens=widgets.FloatSlider(min=0.5, max=10, step=0.5, value=2.0, description='Adh. tape density [g/m]:',readout_format='.1f',layout=layout,style=style)
payloadWeight=widgets.FloatSlider(min=0.0, max=1000.0, step=1, value=0.0, description='Payload weight [g]:',readout_format='.0f',layout=layout,style=style)
    
w = widgets.interactive_output(f, { 'num' : num,
                                    'width' : width,
                                    'heightT' : heightT,
                                    'heightB' : heightB,
                                    'airTemp' : airTemp,
                                    'hotAirTemp' : hotAirTemp,
                                    'coatDens' : coatDens,
                                    'tapeDens' : tapeDens,
                                    'payloadWeight' : payloadWeight
                                  }
                              )

widgets.VBox([num, width, heightT, heightB, airTemp, hotAirTemp, coatDens,tapeDens,payloadWeight, w])
